In [1]:
from libraries import *
from parameters import *
import statsmodels.api as sm

/home/beraslan/miniconda3/lib/python3.8/site-packages/tqdm/auto.py:22: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [2]:
os.getcwd()
os.chdir(projectDir)

In [3]:
adata = sc.read('outputs/anndata/adata-hash-features_singlets_SingleKO_05242020_Filtered.h5ad')


In [4]:
adata.obs[adata.uns['feature_barcode_names']].sum(axis=1).value_counts()

1    325203
dtype: int64

In [5]:
adata.uns['Control_guides'] = [ x for x in adata.uns['feature_barcode_names'] if (x.startswith("ONE_NONGENE_SITE") or x.startswith("NO_TARGET"))]


In [6]:
adataControl = adata[adata.obs[adata.uns['Control_guides']].sum(axis=1) == 1]

In [7]:
expressionMatrix = adataControl.X
expressionMatrix.shape

(41123, 6685)

In [8]:
df = adataControl.obs[["n_genes", "mt_frac", "leiden" ]]
dummies = pd.get_dummies(df.leiden)
df = df.join(dummies)
df.drop(["leiden"], axis=1,inplace = True) 
df.shape

(41123, 12)

In [9]:
guideMatrix = adataControl.obs[adataControl.uns['Control_guides']]
guideMatrix.shape

(41123, 330)

In [10]:
guideMatrix

NO_TARGET_1  NO_TARGET_2  NO_TARGET_3  NO_TARGET_4  \
AAACGCTAGTTGTAGA-1-E3-1             0            0            0            0   
AAAGGATTCAGACAAA-1-E3-1             0            0            0            0   
AAAGGGCAGACGGTTG-1-E3-1             0            0            0            0   
AAAGGGCAGAGATCGC-1-E3-1             0            0            0            0   
AAAGGGCGTTGATGTC-1-E3-1             0            0            0            0   
...                               ...          ...          ...          ...   
TTTGATCCAAACGAGC-1-E4-24            0            0            0            0   
TTTGATCCATGACAAA-1-E4-24            0            0            0            0   
TTTGATCTCAGCTGTA-1-E4-24            0            0            0            0   
TTTGGAGTCCGTAGGC-1-E4-24            0            0            0            0   
TTTGGTTAGTTTAGGA-1-E4-24            0            0            0            0   

                          NO_TARGET_5  NO_TARGET_6  NO_TARGET_7  NO_TARGET_8  \
AAACGCTAGTTGTAGA-1-E3-1             0            0            0            0   
AAAGGATTCAGACAAA-1-E3-1             0            0            0            0   
AAAGGGCAGACGGTTG-1-E3-1             0            0            0            0   
AAAGGGCAGAGATCGC-1-E3-1             0            0            0            0   
AAAGGGCGTTGATGTC-1-E3-1             0            0            0            0   
...                               ...          ...          ...          ...   
TTTGATCCAAACGAGC-1-E4-24            0            0            0            0   
TTTGATCCATGACAAA-1-E4-24            0            0            0            0   
TTTGATCTCAGCTGTA-1-E4-24            0            0            0            0   
TTTGGAGTCCGTAGGC-1-E4-24            0            0            0            0   
TTTGGTTAGTTTAGGA-1-E4-24            0            0            0            0   

                          NO_TARGET_9  NO_TARGET_10  ...  \
AAACGCTAGTTGTAGA-1-E3-1             0             0  ...   
AAAGGATTCAGACAAA-1-E3-1             0             0  ...   
AAAGGGCAGACGGTTG-1-E3-1             0             0  ...   
AAAGGGCAGAGATCGC-1-E3-1             0             0  ...   
AAAGGGCGTTGATGTC-1-E3-1             0             0  ...   
...                               ...           ...  ...   
TTTGATCCAAACGAGC-1-E4-24            0             0  ...   
TTTGATCCATGACAAA-1-E4-24            0             0  ...   
TTTGATCTCAGCTGTA-1-E4-24            0             0  ...   
TTTGGAGTCCGTAGGC-1-E4-24            0             0  ...   
TTTGGTTAGTTTAGGA-1-E4-24            0             0  ...   

                          ONE_NONGENE_SITE_321  ONE_NONGENE_SITE_322  \
AAACGCTAGTTGTAGA-1-E3-1                      0                     0   
AAAGGATTCAGACAAA-1-E3-1                      0                     0   
AAAGGGCAGACGGTTG-1-E3-1                      0                     0   
AAAGGGCAGAGATCGC-1-E3-1                      0                     0   
AAAGGGCGTTGATGTC-1-E3-1                      0                     0   
...                                        ...                   ...   
TTTGATCCAAACGAGC-1-E4-24                     0                     0   
TTTGATCCATGACAAA-1-E4-24                     0                     0   
TTTGATCTCAGCTGTA-1-E4-24                     0                     0   
TTTGGAGTCCGTAGGC-1-E4-24                     0                     0   
TTTGGTTAGTTTAGGA-1-E4-24                     0                     0   

                          ONE_NONGENE_SITE_323  ONE_NONGENE_SITE_324  \
AAACGCTAGTTGTAGA-1-E3-1                      0                     0   
AAAGGATTCAGACAAA-1-E3-1                      0                     0   
AAAGGGCAGACGGTTG-1-E3-1                      0                     0   
AAAGGGCAGAGATCGC-1-E3-1                      0                     0   
AAAGGGCGTTGATGTC-1-E3-1                      0                     0   
...                                        ...                   ...   
TTTGATCCAAACGA

In [11]:
guideMatrix.sum(axis=0)

NO_TARGET_1              80
NO_TARGET_2             183
NO_TARGET_3             119
NO_TARGET_4             174
NO_TARGET_5             216
                       ... 
ONE_NONGENE_SITE_326    126
ONE_NONGENE_SITE_327    148
ONE_NONGENE_SITE_328     72
ONE_NONGENE_SITE_329    118
ONE_NONGENE_SITE_330    318
Length: 330, dtype: int64

In [12]:
guideMatrix.iloc[:,0:50]

NO_TARGET_1  NO_TARGET_2  NO_TARGET_3  NO_TARGET_4  \
AAACGCTAGTTGTAGA-1-E3-1             0            0            0            0   
AAAGGATTCAGACAAA-1-E3-1             0            0            0            0   
AAAGGGCAGACGGTTG-1-E3-1             0            0            0            0   
AAAGGGCAGAGATCGC-1-E3-1             0            0            0            0   
AAAGGGCGTTGATGTC-1-E3-1             0            0            0            0   
...                               ...          ...          ...          ...   
TTTGATCCAAACGAGC-1-E4-24            0            0            0            0   
TTTGATCCATGACAAA-1-E4-24            0            0            0            0   
TTTGATCTCAGCTGTA-1-E4-24            0            0            0            0   
TTTGGAGTCCGTAGGC-1-E4-24            0            0            0            0   
TTTGGTTAGTTTAGGA-1-E4-24            0            0            0            0   

                          NO_TARGET_5  NO_TARGET_6  NO_TARGET_7  NO_TARGET_8  \
AAACGCTAGTTGTAGA-1-E3-1             0            0            0            0   
AAAGGATTCAGACAAA-1-E3-1             0            0            0            0   
AAAGGGCAGACGGTTG-1-E3-1             0            0            0            0   
AAAGGGCAGAGATCGC-1-E3-1             0            0            0            0   
AAAGGGCGTTGATGTC-1-E3-1             0            0            0            0   
...                               ...          ...          ...          ...   
TTTGATCCAAACGAGC-1-E4-24            0            0            0            0   
TTTGATCCATGACAAA-1-E4-24            0            0            0            0   
TTTGATCTCAGCTGTA-1-E4-24            0            0            0            0   
TTTGGAGTCCGTAGGC-1-E4-24            0            0            0            0   
TTTGGTTAGTTTAGGA-1-E4-24            0            0            0            0   

                          NO_TARGET_9  NO_TARGET_10  ...  NO_TARGET_41  \
AAACGCTAGTTGTAGA-1-E3-1             0             0  ...             0   
AAAGGATTCAGACAAA-1-E3-1             0             0  ...             0   
AAAGGGCAGACGGTTG-1-E3-1             0             0  ...             0   
AAAGGGCAGAGATCGC-1-E3-1             0             0  ...             0   
AAAGGGCGTTGATGTC-1-E3-1             0             0  ...             0   
...                               ...           ...  ...           ...   
TTTGATCCAAACGAGC-1-E4-24            0             0  ...             0   
TTTGATCCATGACAAA-1-E4-24            0             0  ...             0   
TTTGATCTCAGCTGTA-1-E4-24            0             0  ...             0   
TTTGGAGTCCGTAGGC-1-E4-24            0             0  ...             0   
TTTGGTTAGTTTAGGA-1-E4-24            0             0  ...             0   

                          NO_TARGET_42  NO_TARGET_43  NO_TARGET_44  \
AAACGCTAGTTGTAGA-1-E3-1              0             0             0   
AAAGGATTCAGACAAA-1-E3-1              0             0             0   
AAAGGGCAGACGGTTG-1-E3-1              0             0             0   
AAAGGGCAGAGATCGC-1-E3-1              0             0             0   
AAAGGGCGTTGATGTC-1-E3-1              0             0             0   
...                                ...           ...           ...   
TTTGATCCAAACGAGC-1-E4-24             0             0             0   
TTTGATCCATGACAAA-1-E4-24             0             0             0   
TTTGATCTCAGCTGTA-1-E4-24             0             0             0   
TTTGGAGTCCGTAGGC-1-E4-24             0             0             0   
TTTGGTTAGTTTAGGA-1-E4-24             0             0             0   

                          NO_TARGET_45  NO_TARGET_46  NO_TARGET_47  \
AAACGCTAGTTGTAGA-1-E3-1              0             0             0   
AAAGGATTCAGACAAA-1-E3-1              0             0             0   
AAAGGGCAGACGGTTG-1-E3-1              0             0             0   
AAAGGGCAGAGATCGC-1-E3-1              0             0             0   
AAAGGGCGTTGATGTC-1-E3-1 

In [13]:
#for elem in guideMatrix.columns:
tmp = pd.DataFrame(guideMatrix.iloc[:,150:200]).join(df)

pvalDF = pd.DataFrame()
coefDF = pd.DataFrame()

for i in range(0,6680,1):
    print(i)
    est = sm.OLS(np.array(expressionMatrix)[:,i], tmp)
    est2 = est.fit().summary2().tables[1]
    pvalDF[str(i)] = est2['P>|t|']
    coefDF[str(i)] = est2['Coef.']

pvalDF.to_csv("ControlGuideEffects/pvalues_150_200_ControlGuide.csv")   
coefDF.to_csv("ControlGuideEffects/coefs_150_200_ControlGuide.csv")   


0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100


/tmp/ipykernel_11317/1247861185.py:11: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  pvalDF[str(i)] = est2['P>|t|']
/tmp/ipykernel_11317/1247861185.py:12: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  coefDF[str(i)] = est2['Coef.']


101


/tmp/ipykernel_11317/1247861185.py:11: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  pvalDF[str(i)] = est2['P>|t|']
/tmp/ipykernel_11317/1247861185.py:12: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  coefDF[str(i)] = est2['Coef.']


102


...

/tmp/ipykernel_11317/1247861185.py:11: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  pvalDF[str(i)] = est2['P>|t|']
/tmp/ipykernel_11317/1247861185.py:12: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  coefDF[str(i)] = est2['Coef.']


6678


/tmp/ipykernel_11317/1247861185.py:11: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  pvalDF[str(i)] = est2['P>|t|']
/tmp/ipykernel_11317/1247861185.py:12: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  coefDF[str(i)] = est2['Coef.']


6679


/tmp/ipykernel_11317/1247861185.py:11: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  pvalDF[str(i)] = est2['P>|t|']
/tmp/ipykernel_11317/1247861185.py:12: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  coefDF[str(i)] = est2['Coef.']
